In [6]:
import os, random
import shutil
import azureml
from azureml.core import Workspace, ComputeTarget, Datastore, Experiment, Dataset, Run, Environment, ScriptRunConfig
from azureml.widgets import RunDetails

In [7]:
workspace = Workspace.from_config()
print(f"Workspace: {workspace.name}")

compute_target = ComputeTarget(workspace=workspace, name="model-training-compute")
print(f"Model Training Compute Target: {compute_target.name}")

default_datastore = Datastore.get_default(workspace)
print(f"Default Datastore: {default_datastore.name}")

model_training_experiment = Experiment(workspace=workspace, name="model-training-experiment")
print(f"Model Training Experiment: {model_training_experiment.name}")

Workspace: faciatraining
Model Training Compute Target: model-training-compute
Default Datastore: workspaceblobstore
Model Training Experiment: model-training-experiment


In [8]:
default_datastore.upload(src_dir="../data", target_path="facial_dataset", overwrite=True, show_progress=True)

"Datastore.upload" is deprecated after version 1.0.69. Please use "Dataset.File.upload_directory" to upload your files             from a local directory and create FileDataset in single method call. See Dataset API change notice at https://aka.ms/dataset-deprecation.


Uploading an estimated of 15988 files
Uploading ../data/.DS_Store
Uploaded ../data/.DS_Store, 1 files out of an estimated total of 15988
Uploading ../data/positive/positive_4591.jpg
Uploaded ../data/positive/positive_4591.jpg, 2 files out of an estimated total of 15988
Uploading ../data/positive/positive_596.jpg
Uploaded ../data/positive/positive_596.jpg, 3 files out of an estimated total of 15988
Uploading ../data/positive/positive_2686.jpg
Uploaded ../data/positive/positive_2686.jpg, 4 files out of an estimated total of 15988
Uploading ../data/positive/positive_3598.jpg
Uploaded ../data/positive/positive_3598.jpg, 5 files out of an estimated total of 15988
Uploading ../data/positive/positive_2692.jpg
Uploaded ../data/positive/positive_2692.jpg, 6 files out of an estimated total of 15988
Uploading ../data/positive/positive_582.jpg
Uploaded ../data/positive/positive_582.jpg, 7 files out of an estimated total of 15988
Uploading ../data/positive/positive_4585.jpg
Uploaded ../data/positiv

$AZUREML_DATAREFERENCE_10dfb92075bf4afaa0c0bce7cd335064

In [9]:
datastore_path = [(default_datastore, "facial_dataset/**" )]
facial_ds = Dataset.File.from_files(path = datastore_path)

In [10]:
facial_ds.register(
    workspace=workspace,
    name = "facial_dataset",
    create_new_version=True
)

{
  "definition": "EnginelessDataflow:\n---\ntype: mltable\npaths:\n  - pattern: \"azureml://subscriptions/21b63490-5de6-4f38-a9c3-cba852c2deed/resourcegroups/FacialVerification/workspaces/faciatraining/datastores/workspaceblobstore/paths/facial_dataset/**\"\nmetadata:\n  infer_column_types: \"False\"\n",
  "registration": {
    "id": "04331365-792f-40d9-aa6f-4b07f15583bb",
    "name": "facial_dataset",
    "version": 1,
    "workspace": "Workspace.create(name='faciatraining', subscription_id='21b63490-5de6-4f38-a9c3-cba852c2deed', resource_group='FacialVerification')"
  }
}

In [11]:
facial_ds = Dataset.get_by_name(workspace, name = "facial_dataset")

In [12]:
pytorch_env = Environment.get(workspace=workspace, name="pytorch-1.6-gpu")
pytorch_env = pytorch_env.clone(new_name='pytorch-1.6-gpu')

In [13]:

args = [
    '--data-folder', facial_ds.as_named_input("facial").as_mount(),
    '--num-epochs', 1,
    '--batch-size', 64,
    '--learning-rate', 1e-3
]

project_folder = "./training_scripts"

config = ScriptRunConfig(
    source_directory = project_folder, 
    script = 'train_azure.py', 
    compute_target=compute_target,
    environment = pytorch_env,
    arguments=args,
)

In [14]:
run = model_training_experiment.submit(config)

In [15]:
RunDetails(run).show()

_UserRunWidget(widget_settings={'childWidgetDisplay': 'popup', 'send_telemetry': False, 'log_level': 'INFO', '…